Lambda School Data Science

*Unit 2, Sprint 3, Module 1*

---


# Define ML problems

You will use your portfolio project dataset for all assignments this sprint.

## Assignment

Complete these tasks for your project, and document your decisions.

- [ ] Choose your target. Which column in your tabular dataset will you predict?
- [ ] Choose which observations you will use to train, validate, and test your model. And which observations, if any, to exclude.
- [ ] Determine whether your problem is regression or classification.
- [ ] Choose your evaluation metric.
- [ ] Begin to clean and explore your data.
- [ ] Begin to choose which features, if any, to exclude. Would some features "leak" information from the future?


In [0]:
import pandas as pd

In [2]:
df = pd.read_csv('/content/VOTER_Survey_December16_Release1.csv')

df.head()

/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (423,564) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


case_identifier    weight  ...      starttime_2016        endtime_2016
0              779  0.358213  ...  29nov2016 22:59:43  29nov2016 23:28:24
1             2108  0.562867  ...  29nov2016 15:41:28  29nov2016 18:58:28
2             2597  0.552138  ...  29nov2016 16:08:39  29nov2016 16:32:43
3             4148  0.207591  ...  14dec2016 18:46:33  14dec2016 19:11:20
4             4460  0.333729  ...  01dec2016 10:17:47  01dec2016 10:59:48

[5 rows x 668 columns]

In [5]:
#classification problem, big issue with imbalanced classes
#I'm inclined to drop the nan rows here
df['turnout16_2016'].value_counts(normalize=True, dropna=False)

Yes    0.951375
No     0.042625
NaN    0.006000
Name: turnout16_2016, dtype: float64

In [6]:
df['turnout16_2016'].value_counts(dropna=False)

Yes    7611
No      341
NaN      48
Name: turnout16_2016, dtype: int64

Let's exclude 2016 survey questions about the specific candidates -- I want to move toward a model that generalizes across different elections. 

2016 questions to include: 
###demographic information
race_2016 -- race

educ_2016 -- max educational attainment

faminc_2016 -- bucketed family income

religpew_2016 -- religion

Sex has to be here somewhere, but I haven't spotted it yet

also: whether voted in 2012! critical!

In [40]:
#people who put "other" on their religious self-ID got a field to write whatever they wanted
df['religpew_t_2016'].value_counts()

__NA__                                                                      7913
Baptist                                                                       10
Christian                                                                      9
Unitarian                                                                      4
Pagan                                                                          4
christian                                                                      3
evangelical                                                                    2
Evangelical                                                                    2
Evangelical Christian                                                          2
Wiccan                                                                         2
babtist                                                                        1
Free will Baptist                                                              1
GOD and Christ              

In [47]:
!pip install pandas-profiling

In [0]:
import pandas_profiling

In [51]:
#reading the data dictionary for this is exactly as tedious as you would imagine
pandas_profiling.ProfileReport(df)

#Checking Voter History dataset

In [0]:
heads = ['voter_id','status_code','party_code','last_name','first_name','middle_name',
        'prefix','suffix','sex','street_no','suffix_a','suffix_b','street_name',
        'unit_no','street_name2','street_name3','city','state','zip5','zip4',
        'mail_street_no','mail_suffa','mail_suffb','mail_street_name1','mail_unit_no',
        'mail_street_name2','mail_street_name3','mail_city','mail_state','mail_country',
        'mail_zip','birthdate','registered','ballot','county','municipality','ward',
        'district','party_voted','municipality_voted','ward_voted','district_voted',
        'election_date','election_name','election_type','election_cat','0','1']

In [25]:
vh = pd.read_csv('/content/VoterHistory2.csv',names=heads)

vh.head()

/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (0,9,11,20,21,22,25,40,46) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


voter_id status_code party_code  ... election_cat    0   1
0  117152599           A        UNA  ...            S  NaN NaN
1  117126106           A        REP  ...            S  NaN NaN
2  117117093           A        UNA  ...            S  NaN NaN
3  117088849           A        REP  ...            S  NaN NaN
4  117088849           A        REP  ...            S  NaN NaN

[5 rows x 48 columns]

In [16]:
vh.shape

(38095, 48)

In [31]:
vh['0'].value_counts(dropna=False)

NaN    38094
S          1
Name: 0, dtype: int64

In [29]:
#one misaligned row 
vh['election_name'].value_counts(dropna=False)

GENERAL ELECTION    22427
PRIMARY ELECTION     9118
NaN                  6549
11/08/2016              1
Name: election_name, dtype: int64

In [35]:
vh['election_type'].value_counts(dropna=False)

GEN                 22427
PRI                  9118
NaN                  6549
GENERAL ELECTION        1
Name: election_type, dtype: int64

In [44]:
#identifying the rogue row to fix it in numbers and re-upload
#surely there's a way to do this in pandas?
npri = vh[vh['election_type'] != 'PRI']

npri.shape

(28977, 48)

In [46]:
ngen = npri[npri['election_type'] != 'GEN']

ngen.head()

voter_id status_code party_code  ... election_cat    0   1
10  151522196          IF        UNA  ...          NaN  NaN NaN
11  150021815          IF        UNA  ...          NaN  NaN NaN
17  117084564          IF        DEM  ...          NaN  NaN NaN
22  117058758           A        DEM  ...          NaN  NaN NaN
25  150817841           A        UNA  ...          NaN  NaN NaN

[5 rows x 48 columns]

In [52]:
problem = npri[npri['election_type'] == 'GENERAL ELECTION']

problem

voter_id status_code party_code  ... election_cat  0   1
2761  532945835           A        DEM  ...          GEN  S NaN

[1 rows x 48 columns]

In [54]:
vh['municipality_voted'].value_counts(dropna=False)

NORTH PLAINFIELD         14891
MANVILLE BOROUGH          8309
GREEN BROOK               7097
NaN                       6549
PLAINFIELD                 181
PISCATAWAY                  57
BRIDGEWATER TWP             52
HILLSBOROUGH                50
UNION                       48
FRANKLIN TWP                40
SCOTCH PLAINS               38
NEWARK                      34
JERSEY CITY                 31
WOODBRIDGE                  31
BOUND BROOK                 27
ELIZABETH                   27
SOUTH BOUND BROOK           26
WARREN                      24
DUNELLEN                    24
ROSELLE                     24
EDISON                      20
SOUTH PLAINFIELD            20
WATCHUNG BOROUGH            20
IRVINGTON                   20
RARITAN                     16
MAPLEWOOD                   14
CRANFORD                    13
SOMERVILLE                  13
MIDDLESEX                   12
HILLSIDE                    11
                         ...  
EGG HARBOR TWP               1
LITTLE F

In [56]:
vh = pd.read_csv('/content/VoterHistory3.csv',names=heads)

vh.head()

/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (0,9,11,20,21,22,25) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


voter_id status_code party_code  ... election_cat   0   1
0  117152599           A        UNA  ...            S NaN NaN
1  117126106           A        REP  ...            S NaN NaN
2  117117093           A        UNA  ...            S NaN NaN
3  117088849           A        REP  ...            S NaN NaN
4  117088849           A        REP  ...            S NaN NaN

[5 rows x 48 columns]

In [57]:
pandas_profiling.ProfileReport(vh)
"""
important notes:
-looks like missing birthdays are filled in as january 1, 1800. that's awful!
-city has some inconsistent all caps -- green brook should be made to == GREEN BROOK
-there are records for five elections: 6.2.2015, 6.7.2016, 11.8.2016, 6.6.2017, and 11.8.2016
    06/02/2015, Primary--PRIMARY ELECTION
    06/07/2016, Primary--PRIMARY ELECTION
    11/08/2016, General--GENERAL ELECTION
    06/06/2017, Primary--PRIMARY ELECTION
    11/07/2017, General--GENERAL ELECTION 
-there are a number of third party codes in addition to dem, rep, and una (unaffiliated)
-I don't immediately spot any fake registration dates
-voter id number frequency maxes out at five, as would be expected
--this is probably the value to merge on, if necessary!


/usr/local/lib/python3.6/dist-packages/pandas/core/algorithms.py:829: UserWarning: Unable to sort modes: '<' not supported between instances of 'int' and 'str'
  warn("Unable to sort modes: {error}".format(error=e))
